In [1]:
import os

os.environ["CUDA_DEVICE_ORDER"] = "PCI_BUS_ID"
os.environ["CUDA_VISIBLE_DEVICES"] = "2"

In [2]:
from monty.serialization import loadfn, dumpfn

In [4]:
from ase.filters import FrechetCellFilter
from ase.optimize import LBFGS
from pymatgen.io.ase import AseAtomsAdaptor
from orb_models.forcefield import pretrained
from orb_models.forcefield.calculator import ORBCalculator
from fairchem.core import pretrained_mlip, FAIRChemCalculator

In [5]:
MODEL = "orb" # "orb" or "uma"

In [7]:
orb_ff = pretrained.orb_v3_conservative_inf_omat(device="cuda",precision="float32-high")  # or "float32-highest" / "float64
orb_calc = ORBCalculator(orb_ff, device="cuda")

uma_ff = pretrained_mlip.get_predict_unit("uma-m-1p1", device="cuda")
uma_calc = FAIRChemCalculator(uma_ff, task_name="omat")

MODELS = {
    "orb":orb_calc,
    "uma": uma_calc
}

In [8]:
import torch._dynamo
torch._dynamo.config.suppress_errors = True

In [9]:
def relax_structure(structure): # takes in pymatgen structure
    atoms = structure.to_ase_atoms()
    atoms.calc = MODELS[MODEL]

    opt = LBFGS(FrechetCellFilter(atoms))# Delete this FrechetCellFilter when doing the defect structures, need FrechetCellFilter when doing competing phases
    opt.run(0.01, 1000)

    structure1 = AseAtomsAdaptor.get_structure(atoms)
    energy = atoms.get_potential_energy()

    return structure1, energy 

In [10]:
from doped.chemical_potentials import CompetingPhases
from pymatgen.entries.computed_entries import ComputedEntry
from doped.chemical_potentials import CompetingPhasesAnalyzer

In [11]:
calculated_entries = {}

def calc_competing_phase(comp): # Pass in formula of species
    cp = CompetingPhases(composition=comp, extrinsic='Cr', energy_above_hull=0.05)
    entries = []
    for entry in cp.entries:
        key =  entry.data['material_id'] + entry.structure.composition.reduced_formula
        
        if key in calculated_entries:
            new_entry = calculated_entries[key]
        else:
            relaxed_structure, energy = relax_structure(entry.structure)
            new_entry = ComputedEntry(
                relaxed_structure.composition,
                energy, 
                data = {'material_id':entry.data['material_id']}
            )
            calculated_entries[key] = new_entry 
        entries.append(new_entry)
        
    return cp, entries # maybe dont have to return cp

In [12]:
def calc_competing_phase_analysis(comp, entries):
    
    cpa = CompetingPhasesAnalyzer(composition=comp, entries=entries)
    
    return cpa.chempots

In [13]:
relaxed_defect = loadfn(f'../data/{MODEL}_doped_defect_energies.json')

In [14]:
for key, val in relaxed_defect.items():
    formula = val['formula']
    cp, entries = calc_competing_phase(formula) # do you have to return cp?
    chem_pot = calc_competing_phase_analysis(formula, entries)
    if 'competing phases' not in relaxed_defect[key]:
        relaxed_defect[key]['competing phases'] = {}
    relaxed_defect[key]['competing phases']['chemical potentials'] = chem_pot
    relaxed_defect[key]['competing phases']['entries'] = entries

Duplicate entry names found for generated competing phases: AlPO4_Pbca_EaH_0.012!
Duplicate entry names found for generated competing phases: AlPO4_Pbca_EaH_0.012!
W0728 15:56:18.115000 32181 site-packages/torch/_inductor/utils.py:1137] [0/0] Not enough SMs to use max_autotune_gemm mode
W0728 15:56:18.563000 32181 site-packages/torch/_dynamo/convert_frame.py:1233] WON'T CONVERT forward /home/atshaam/miniconda3/envs/project_env/lib/python3.11/site-packages/orb_models/forcefield/gns.py line 421 
W0728 15:56:18.563000 32181 site-packages/torch/_dynamo/convert_frame.py:1233] due to: 
W0728 15:56:18.563000 32181 site-packages/torch/_dynamo/convert_frame.py:1233] Traceback (most recent call last):
W0728 15:56:18.563000 32181 site-packages/torch/_dynamo/convert_frame.py:1233]   File "/home/atshaam/miniconda3/envs/project_env/lib/python3.11/site-packages/torch/_dynamo/convert_frame.py", line 1164, in __call__
W0728 15:56:18.563000 32181 site-packages/torch/_dynamo/convert_frame.py:1233]     re

       Step     Time          Energy          fmax
LBFGS:    0 15:56:26     -380.965393        0.066072


logm result may be inaccurate, approximate err = 4.726475621142667e-13


LBFGS:    1 15:56:26     -380.966339        0.055532


logm result may be inaccurate, approximate err = 4.705367813335809e-13


...

logm result may be inaccurate, approximate err = 6.300415075478755e-13
logm result may be inaccurate, approximate err = 6.322748471310783e-13


       Step     Time          Energy          fmax
LBFGS:    0 16:52:17    -1086.387451        0.795710
LBFGS:    1 16:52:17    -1086.685181        0.460077
LBFGS:    2 16:52:17    -1086.896729        0.421112
LBFGS:    3 16:52:17    -1086.966797        0.404045
LBFGS:    4 16:52:17    -1087.096558        0.385939
LBFGS:    5 16:52:17    -1087.131836        0.383166
LBFGS:    6 16:52:17    -1087.256592        0.865363
LBFGS:    7 16:52:18    -1087.362671        0.798312
LBFGS:    8 16:52:18    -1087.507690        0.771294
LBFGS:    9 16:52:18    -1085.585327        6.702530
LBFGS:   10 16:52:18    -1087.675781        0.538567
LBFGS:   11 16:52:18    -1087.720825        0.356687
LBFGS:   12 16:52:18    -1087.802002        0.503003
LBFGS:   13 16:52:19    -1087.849121        0.640617
LBFGS:   14 16:52:19    -1087.417480        4.780460
LBFGS:   15 16:52:19    -1088.035767        0.742030
LBFGS:   16 16:52:19    -1088.163818        0.730059
LBFGS:   17 16:52:19    -1087.569946        3.03

Duplicate entry names found for generated competing phases: Al2(MoO4)3_NA_EaH_0!


       Step     Time          Energy          fmax
LBFGS:    0 16:53:32     -206.891083        0.097577
LBFGS:    1 16:53:32     -206.891998        0.059883
LBFGS:    2 16:53:32     -206.892700        0.041951
LBFGS:    3 16:53:32     -206.892761        0.041255
LBFGS:    4 16:53:32     -206.893051        0.037027
LBFGS:    5 16:53:32     -206.893143        0.034649
LBFGS:    6 16:53:32     -206.893311        0.029208
LBFGS:    7 16:53:32     -206.893448        0.024100
LBFGS:    8 16:53:32     -206.893585        0.018763
LBFGS:    9 16:53:32     -206.893661        0.015260
LBFGS:   10 16:53:33     -206.893723        0.012675
LBFGS:   11 16:53:33     -206.893768        0.010433
LBFGS:   12 16:53:33     -206.893799        0.010390
LBFGS:   13 16:53:33     -206.893845        0.010640
LBFGS:   14 16:53:33     -206.893860        0.008869
       Step     Time          Energy          fmax
LBFGS:    0 16:53:33       -7.433372        0.133231
LBFGS:    1 16:53:33       -7.433739        0.1227

Duplicate entry names found for generated competing phases: Al2O3_NA_EaH_0.0308!


In [15]:
dumpfn(relaxed_defect, f'../data/{MODEL}_doped_defect_energies.json')